In [5]:
import numpy as np
from numpy import sin, cos, deg2rad
import plotly.graph_objects as go
from plotly.subplots import make_subplots

from find_ipctk import ipctk

In [6]:
import parula as par
import matplotlib
from matplotlib import cm

parula_cmap = par.parula_map

parula_rgb = []
norm = matplotlib.colors.Normalize(vmin=0, vmax=255)

for i in range(0, 255):
    k = matplotlib.colors.colorConverter.to_rgb(parula_cmap(norm(i)))
    parula_rgb.append(k)


def matplotlib_to_plotly(cmap, pl_entries):
    h = 1.0/(pl_entries-1)
    pl_colorscale = []

    for k in range(pl_entries):
        C = list(map(np.uint8, np.array(cmap(k*h)[:3])*255))
        pl_colorscale.append([k*h, f'rgb({C[0]}, {C[1]}, {C[2]})'])

    return pl_colorscale


parula = matplotlib_to_plotly(parula_cmap, 255)

In [7]:
vertices = np.array([[-1, 0], [0, 0], [1, 0]], dtype=float)
edges = [[0, 1], [1, 2]]
dhat = 0.5

dhat_a = 0.5
dhat_p = 0.5 * dhat_a
Y = 1
eps_c = 0.5
a2 = Y * eps_c / (2 * (dhat_p - dhat_a))
print(a2)


def potential(d2):
    return (np.sqrt(d2)/dhat - 1)**2 if d2 < dhat**2 else 0
    # return ipctk.normal_adhesion_potential(np.sqrt(d2), 0.5 * dhat, dhat, a2)


def sum_max_approximator(x):
    return sum([potential(ipctk.point_edge_distance(x, vertices[e[0]], vertices[e[1]])) for e in edges])


def improved_max_approximator(x):
    return sum_max_approximator(x) - potential(ipctk.point_point_distance(vertices[1], x))


def Lp_max_approximator(x, p=10):
    return sum([potential(np.abs(ipctk.point_edge_distance(x, vertices[e[0]], vertices[e[1]])))**p for e in edges])**(1/p)


def actual_max(x):
    return max([potential(ipctk.point_edge_distance(x, vertices[e[0]], vertices[e[1]])) for e in edges])

-1.0


In [8]:
n = 128
xs = np.linspace(-1.5, 1.5, n)
ys = np.linspace(-1.5, 1.5, n)


def z(op):
    z = np.empty((n, n))
    for j, x in enumerate(xs):
        for i, y in enumerate(ys):
            z[i, j] = op(np.array([x, y]))  # - actual_max(np.array([x, y]))
    return z


fig = make_subplots(
    rows=4, cols=4,
    subplot_titles=("Sum [Li et al. 2020]", "Exact", "Ours", "Lᵖ"),
    horizontal_spacing=0.05, vertical_spacing=0.05
)


def plot_row(row):
    for i, op in enumerate([sum_max_approximator, actual_max, improved_max_approximator, Lp_max_approximator]):
        fig.add_trace(go.Heatmap(
            z=z(op), x=xs, y=ys,
            # contours=dict(start=-1e-12, end=1),
            # zmin=0, zmax=0.12,
            zmin=0, zmax=1,
            # zmax=potential(2*dhat), zmin=potential(0),
            colorscale=parula,
            # line_smoothing=0
        ), row=row, col=i+1)
        fig.add_trace(go.Scatter(
            x=vertices[:, 0], y=vertices[:, 1], mode='markers',
            line=dict(width=2, color='black'),
            marker=dict(size=5, line=dict(
                width=2, color='black'), color='yellow'),
        ), row=row, col=i+1)


def update_angle(theta):
    vertices[2] = [cos(deg2rad(180 - theta)), sin(deg2rad(180 - theta))]


update_angle(180)
plot_row(1)
update_angle(135)
plot_row(2)
update_angle(90)
plot_row(3)
update_angle(45)
plot_row(4)

fig.update_layout(
    width=1200, height=1200,
    yaxis_title='180°', yaxis5_title='135°', yaxis9_title='90°', yaxis13_title='45°',
    showlegend=False
)
fig.show()